In [1]:
import json
import pandas as pd
import pickle
import plotly.express as px

In [2]:
with open('data/brasil_estados.geojson') as geoj:
    brasil = json.load(geoj)

In [3]:
brasil['features'][0]

{'type': 'Feature',
 'geometry': {'type': 'MultiPolygon',
  'coordinates': [[[[-73.800983, -7.111458],
     [-73.737625, -7.134317],
     [-72.900612, -7.436948],
     [-72.58801, -7.55025],
     [-72.302927, -7.584565],
     [-72.168962, -7.600226],
     [-71.957815, -7.624875],
     [-71.381112, -7.691941],
     [-71.087929, -7.725894],
     [-70.515259, -7.791927],
     [-70.132606, -7.835827],
     [-70.051806, -7.847004],
     [-69.801148, -8.060751],
     [-69.442709, -8.366957],
     [-69.212413, -8.563997],
     [-68.922336, -8.812517],
     [-68.646622, -9.049037],
     [-68.219776, -9.242135],
     [-67.974448, -9.353164],
     [-67.51684, -9.560291],
     [-67.325494, -9.59196],
     [-67.324358, -9.592393],
     [-67.133064, -9.676151],
     [-66.8097, -9.817661],
     [-66.624418, -9.898736],
     [-66.626585, -9.901427],
     [-66.623527, -9.905862],
     [-66.635253, -9.912935],
     [-66.627059, -9.917489],
     [-66.625914, -9.921128],
     [-66.632223, -9.922143],
   

In [6]:
brasil['features'][0]['geometry']['coordinates'][0][0]

[[-73.800983, -7.111458],
 [-73.737625, -7.134317],
 [-72.900612, -7.436948],
 [-72.58801, -7.55025],
 [-72.302927, -7.584565],
 [-72.168962, -7.600226],
 [-71.957815, -7.624875],
 [-71.381112, -7.691941],
 [-71.087929, -7.725894],
 [-70.515259, -7.791927],
 [-70.132606, -7.835827],
 [-70.051806, -7.847004],
 [-69.801148, -8.060751],
 [-69.442709, -8.366957],
 [-69.212413, -8.563997],
 [-68.922336, -8.812517],
 [-68.646622, -9.049037],
 [-68.219776, -9.242135],
 [-67.974448, -9.353164],
 [-67.51684, -9.560291],
 [-67.325494, -9.59196],
 [-67.324358, -9.592393],
 [-67.133064, -9.676151],
 [-66.8097, -9.817661],
 [-66.624418, -9.898736],
 [-66.626585, -9.901427],
 [-66.623527, -9.905862],
 [-66.635253, -9.912935],
 [-66.627059, -9.917489],
 [-66.625914, -9.921128],
 [-66.632223, -9.922143],
 [-66.635528, -9.928381],
 [-66.63153, -9.927272],
 [-66.632857, -9.929271],
 [-66.626609, -9.931589],
 [-66.626998, -9.935368],
 [-66.632887, -9.936909],
 [-66.637611, -9.951763],
 [-66.65, -9.945137

In [7]:
df = dict()
for i in brasil['features']:
    estado = i['properties']['uf_05']
    geocodigo = i['properties']['geocodigo']
    
    df[estado] = [geocodigo]

print(df)

{'AC': ['12'], 'AL': ['27'], 'AM': ['13'], 'AP': ['16'], 'BA': ['29'], 'CE': ['23'], 'ES': ['32'], 'GO': ['52'], 'MA': ['21'], 'PA': ['15'], 'MG': ['31'], 'MS': ['50'], 'MT': ['51'], 'PB': ['25'], 'PE': ['26'], 'PI': ['22'], 'PR': ['41'], 'RJ': ['33'], 'RN': ['24'], 'RO': ['11'], 'RR': ['14'], 'RS': ['43'], 'SC': ['42'], 'SE': ['28'], 'SP': ['35'], 'TO': ['17'], 'DF': ['53']}


In [8]:
for estado in df.keys():
    with open('metrics/{}_hdi.pkl'.format(estado), 'rb') as f:
        hdi = pickle.load(f)
    
    df[estado].append(hdi['Low'])
    df[estado].append(hdi['High'])

df = pd.DataFrame.from_dict(df, orient='index', columns = ['geocodigo', 'Low', 'High'])

In [9]:
df

geocodigo   Low  High
AC        12  0.84  1.22
AL        27  0.83  1.03
AM        13  0.87  1.07
AP        16  0.42  0.62
BA        29  1.22  1.36
CE        23  1.17  1.29
ES        32  1.04  1.21
GO        52  0.91  1.11
MA        21  0.94  1.11
PA        15  0.87  1.00
MG        31  1.63  1.78
MS        50  1.02  1.36
MT        51  1.09  1.32
PB        25  1.13  1.29
PE        26  0.77  0.98
PI        22  1.02  1.24
PR        41  1.00  1.21
RJ        33  0.94  1.07
RN        24  1.05  1.24
RO        11  1.10  1.36
RR        14  1.55  1.77
RS        43  1.20  1.41
SC        42  1.26  1.46
SE        28  1.02  1.27
SP        35  1.15  1.22
TO        17  0.93  1.29
DF        53  1.06  1.22

In [11]:
fig = px.choropleth_mapbox(df, geojson=brasil, color="High",
                           locations="geocodigo", featureidkey="properties.geocodigo",
                           center={"lat": -15.5517, "lon": -58.7073},
                           mapbox_style="carto-positron", zoom=3)
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()


In [16]:
import folium

m = folium.Map(location=[-15, -58], zoom_start=3)

folium.Choropleth(
    geo_data=brasil,
    name='choropleth',
    data=df,
    columns=['geocodigo', 'High'],
    key_on='properties.geocodigo',
    fill_color='Reds',
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name='Rt',
).add_to(m)

folium.LayerControl().add_to(m)

m